In [17]:
import gensim
from gensim.models.doc2vec import Doc2Vec, TaggedDocument
from textScrapper import TextScrapper
from tqdm import tqdm
import numpy as np
import os
from nltk.tokenize import word_tokenize
from nltk.tokenize import sent_tokenize
import string
import re
import warnings
from sklearn.model_selection import train_test_split
warnings.filterwarnings('ignore')

In [5]:
# exemple path file ../data/sncf_vinci_ifg_62/00086570-002601E-B007-20220323-R-VEN.pdf
class fileTextManager():
    
    def __init__ (self):
        self.current_DB= "sncf_vinci_ifg_62"
        
        
    def cleanText(self, text):
        char="abcdefghijklmnopqrstuvwxyzéèàçôùëïüäîê.' "
        lowercaseText= text[0].lower()
        cleanText = ""
        for letter in lowercaseText:
            if letter in char:
                cleanText = cleanText + letter
        return cleanText

    def getExtension(self, file):
        filename, file_extension = os.path.splitext(file)
        return file_extension
    
    
    def getFileText(self, file):
        textScrap = TextScrapper()
        typeDocumentNumber=[]
        match file["mimeType"]:
            case 'application/pdf':
                try:
                    fullText = textScrap.getTextPdf(f"/Volumes/DD Thibault/sncf_DB/doc/{self.current_DB}/{file['KidFile']}")
                except:
                    fullText = None
                fullText = self.cleanText(fullText)
                return fullText
            case 'application/vnd.ms-excel':
                
                fullText = textScrap.getTextExcel(f"/Volumes/DD Thibault/sncf_DB/doc/{self.current_DB}/{file['KidFile']}")
                return fullText

            case 'application/vnd.openxmlformats-officedocument.wordprocessingml.document':
                fullText = textScrap.getTextWord(f"/Volumes/DD Thibault/sncf_DB/doc/{self.current_DB}/{file['KidFile']}")
                return fullText
            
            #case 'application/vnd.openxmlformats-officedocument.spreadsheetml.sheet':
                #fullText = textScrap.getTextWord(f"/Volumes/DD Thibault/sncf_DB/doc/engie/{file['KidFile']}")
                #return fullText
            #case 'image/jpeg':
                #return 2

            case _:
                return 'document type not supported'
                #raise ValueError('document type not supported')   # 0 is the default case if x is not found
    

In [6]:
csvPath = "/Volumes/DD Thibault/sncf_DB/doc/sncf_vinci_ifg_62.csv"
scrapper = TextScrapper()
csv = scrapper.getTextCsv(csvPath)
dictPdfWord=[]
fileManager = fileTextManager()
print(len(csv))
print(csv.iloc[4])
for row in tqdm((csv.iloc)):
    if row["mimeType"] == "application/pdf" or row["mimeType"] == "application/vnd.openxmlformats-officedocument.wordprocessingml.document":
        contentFile = fileManager.getFileText(row)
        #TODO charge content by batch
        newFile = {"fileName": row["fileName"], "mimeType": row["mimeType"], "content": contentFile}
        dictPdfWord.append(newFile["content"])
print(len(dictPdfWord))
print(dictPdfWord[0])
data, test_data = train_test_split(dictPdfWord,test_size=0.15)
  

2470
fileName                   4129K-B006-GAZ.pdf
KidDocumentClass       K_NODE;cATERTETANCHGAZ
fileSize                               799744
mimeType                      application/pdf
owner               PROFIL;0001015M0324LV55BY
creationDate              2021-02-04 14:58:55
KidFile             K_NODE;0022805M2U19ARDWQT
Name: 4, dtype: object


2470it [05:07,  8.03it/s]

2470
  rapport dintervention   contrôle de létanchéité  du rés eau  gaz  n   date du rapport    n de fiche    client   sncf   site   nbbrigade voie  adresse   malesherbes gare  malesherbes  responsable affaire   mustapha khallouk  responsable technique     certificat d étanchéité   je soussigné abdelouahid  daoudi  avoir effectué le contrôle  de létanchéité  du réseau gaz entre le point de livraison du site  à léquipement de production .  statut de létanchéité du réseau de gaz   étanche   observation    cuve  pour aiguille non étanche signalé à m.guymar   technicien vinci facilities  nom et signature  signature client  abdelouahid  daoudi  abdelouahid.daoudivinci facilities.com           


In [7]:
print(sent_tokenize(data[0]))
dataSent = []
for file in tqdm(data):
    if isinstance(file, str):
        dataSent.append(sent_tokenize(file))
print(dataSent[0])
dataWord = []
for fileSent in tqdm(dataSent):
    sentWord = []
    for sent in fileSent:
        
        if isinstance(sent, str):
            sentWord.append(word_tokenize(sent))
    dataWord.append(sentWord)
    
    
print(dataWord[0])


["votre centre de contact client vous informemadame monsieurdans le cadre de votre contrat  nous vous informons que notre technicien est intervenu sur l'équipement  réf kone   situé sncf  facade arriere garagerue de la gare saint pellerinles opérations de maintenance suivantes ont été réalisés le  par rointru sylvain cette visite comprend la vérification lubrification réglage des éléments suivants   dispositifs de sécurité  barres palpeuses cellules  débrayage manuel  limiteur deffort  articulations charnières  pivots  zone daccostage  signalisation  feux clignotants éclairage marquage au sol  transmission bras  cbles chaines courroies  opérateur  motoréducteur opérateur hydro électriquecommentaires votre centre de contact client kone tél      signature client    notice  les informations contenues dans ce message sont à l'attention exclusive des personnes désignées.", 'elles peuvent contenir des informations confidentielles.', "si vous n'en êtes pas le destinataire toute utilisation co

100%|██████████████████████████████████████████████████████████████████████████| 2099/2099 [00:00<00:00, 5426.40it/s]


["votre centre de contact client vous informemadame monsieurdans le cadre de votre contrat  nous vous informons que notre technicien est intervenu sur l'équipement  réf kone   situé sncf  facade arriere garagerue de la gare saint pellerinles opérations de maintenance suivantes ont été réalisés le  par rointru sylvain cette visite comprend la vérification lubrification réglage des éléments suivants   dispositifs de sécurité  barres palpeuses cellules  débrayage manuel  limiteur deffort  articulations charnières  pivots  zone daccostage  signalisation  feux clignotants éclairage marquage au sol  transmission bras  cbles chaines courroies  opérateur  motoréducteur opérateur hydro électriquecommentaires votre centre de contact client kone tél      signature client    notice  les informations contenues dans ce message sont à l'attention exclusive des personnes désignées.", 'elles peuvent contenir des informations confidentielles.', "si vous n'en êtes pas le destinataire toute utilisation co

100%|███████████████████████████████████████████████████████████████████████████| 2098/2098 [00:02<00:00, 805.10it/s]

[['votre', 'centre', 'de', 'contact', 'client', 'vous', 'informemadame', 'monsieurdans', 'le', 'cadre', 'de', 'votre', 'contrat', 'nous', 'vous', 'informons', 'que', 'notre', 'technicien', 'est', 'intervenu', 'sur', "l'équipement", 'réf', 'kone', 'situé', 'sncf', 'facade', 'arriere', 'garagerue', 'de', 'la', 'gare', 'saint', 'pellerinles', 'opérations', 'de', 'maintenance', 'suivantes', 'ont', 'été', 'réalisés', 'le', 'par', 'rointru', 'sylvain', 'cette', 'visite', 'comprend', 'la', 'vérification', 'lubrification', 'réglage', 'des', 'éléments', 'suivants', 'dispositifs', 'de', 'sécurité', 'barres', 'palpeuses', 'cellules', 'débrayage', 'manuel', 'limiteur', 'deffort', 'articulations', 'charnières', 'pivots', 'zone', 'daccostage', 'signalisation', 'feux', 'clignotants', 'éclairage', 'marquage', 'au', 'sol', 'transmission', 'bras', 'cbles', 'chaines', 'courroies', 'opérateur', 'motoréducteur', 'opérateur', 'hydro', 'électriquecommentaires', 'votre', 'centre', 'de', 'contact', 'client', '

In [9]:
dictionary = []
for fileWord in tqdm(dataWord):
    dictionary.append(gensim.corpora.Dictionary(fileWord))

print(dictionary[0].token2id)

100%|██████████████████████████████████████████████████████████████████████████| 2098/2098 [00:00<00:00, 2838.07it/s]

{'.': 0, 'arriere': 1, 'articulations': 2, 'au': 3, 'barres': 4, 'bras': 5, 'cadre': 6, 'cbles': 7, 'ce': 8, 'cellules': 9, 'centre': 10, 'cette': 11, 'chaines': 12, 'charnières': 13, 'client': 14, 'clignotants': 15, 'comprend': 16, 'contact': 17, 'contenues': 18, 'contrat': 19, 'courroies': 20, 'daccostage': 21, 'dans': 22, 'de': 23, 'deffort': 24, 'des': 25, 'dispositifs': 26, 'débrayage': 27, 'désignées': 28, 'est': 29, 'exclusive': 30, 'facade': 31, 'feux': 32, 'garagerue': 33, 'gare': 34, 'hydro': 35, 'informations': 36, 'informemadame': 37, 'informons': 38, 'intervenu': 39, 'kone': 40, "l'attention": 41, "l'équipement": 42, 'la': 43, 'le': 44, 'les': 45, 'limiteur': 46, 'lubrification': 47, 'maintenance': 48, 'manuel': 49, 'marquage': 50, 'message': 51, 'monsieurdans': 52, 'motoréducteur': 53, 'notice': 54, 'notre': 55, 'nous': 56, 'ont': 57, 'opérateur': 58, 'opérations': 59, 'palpeuses': 60, 'par': 61, 'pellerinles': 62, 'personnes': 63, 'pivots': 64, 'que': 65, 'rointru': 66, 

In [10]:
corpus= []
i=0
for fileWord in tqdm(dataWord):
    sentBow = []
    for sentWord in fileWord:
        sentBow.append(dictionary[i].doc2bow(sentWord))
    corpus.append(sentBow)
    i+=1
print(corpus[0])

100%|██████████████████████████████████████████████████████████████████████████| 2098/2098 [00:00<00:00, 5996.80it/s]

[[(0, 1), (1, 1), (2, 1), (3, 1), (4, 1), (5, 1), (6, 1), (7, 1), (8, 1), (9, 1), (10, 2), (11, 1), (12, 1), (13, 1), (14, 3), (15, 1), (16, 1), (17, 2), (18, 1), (19, 1), (20, 1), (21, 1), (22, 1), (23, 6), (24, 1), (25, 2), (26, 1), (27, 1), (28, 1), (29, 1), (30, 1), (31, 1), (32, 1), (33, 1), (34, 1), (35, 1), (36, 1), (37, 1), (38, 1), (39, 1), (40, 2), (41, 1), (42, 1), (43, 2), (44, 2), (45, 1), (46, 1), (47, 1), (48, 1), (49, 1), (50, 1), (51, 1), (52, 1), (53, 1), (54, 1), (55, 1), (56, 1), (57, 1), (58, 2), (59, 1), (60, 1), (61, 1), (62, 1), (63, 1), (64, 1), (65, 1), (66, 1), (67, 1), (68, 1), (69, 1), (70, 1), (71, 1), (72, 1), (73, 1), (74, 1), (75, 1), (76, 1), (77, 1), (78, 1), (79, 1), (80, 1), (81, 1), (82, 1), (83, 1), (84, 1), (85, 1), (86, 3), (87, 2), (88, 1), (89, 1), (90, 1), (91, 1), (92, 1), (93, 1), (94, 1)], [(0, 1), (25, 1), (36, 1), (95, 1), (96, 1), (97, 1), (98, 1)], [(0, 1), (23, 1), (44, 1), (76, 1), (87, 1), (99, 1), (100, 1), (101, 1), (102, 1), (103

In [18]:
i=0
for fileCorpus in corpus:
    tfidf = gensim.models.TfidfModel(fileCorpus)
    
    sentBow = []
    for doc in tfidf[fileCorpus]:
        print([[dictionary[id], np.around(freq, decimals=2)] for id, freq in doc])
    corpus.append(sentBow)
    i+=1
print(corpus[0])

[[<gensim.corpora.dictionary.Dictionary object at 0x12ac134f0>, 0.09], [<gensim.corpora.dictionary.Dictionary object at 0x111cfa650>, 0.09], [<gensim.corpora.dictionary.Dictionary object at 0x111cfb3a0>, 0.09], [<gensim.corpora.dictionary.Dictionary object at 0x111cf91b0>, 0.09], [<gensim.corpora.dictionary.Dictionary object at 0x12c1c4130>, 0.09], [<gensim.corpora.dictionary.Dictionary object at 0x12c1c6aa0>, 0.09], [<gensim.corpora.dictionary.Dictionary object at 0x12c1c5630>, 0.09], [<gensim.corpora.dictionary.Dictionary object at 0x12c1c7a00>, 0.05], [<gensim.corpora.dictionary.Dictionary object at 0x12c1c5d50>, 0.09], [<gensim.corpora.dictionary.Dictionary object at 0x12c1c6920>, 0.17], [<gensim.corpora.dictionary.Dictionary object at 0x12c1c5ea0>, 0.09], [<gensim.corpora.dictionary.Dictionary object at 0x12c1c5360>, 0.09], [<gensim.corpora.dictionary.Dictionary object at 0x12c1c7130>, 0.09], [<gensim.corpora.dictionary.Dictionary object at 0x12c1c6110>, 0.26], [<gensim.corpora.di

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



[[<gensim.corpora.dictionary.Dictionary object at 0x12ac134f0>, 0.09], [<gensim.corpora.dictionary.Dictionary object at 0x111cfa650>, 0.09], [<gensim.corpora.dictionary.Dictionary object at 0x111cfb3a0>, 0.09], [<gensim.corpora.dictionary.Dictionary object at 0x111cf91b0>, 0.09], [<gensim.corpora.dictionary.Dictionary object at 0x12c1c4130>, 0.09], [<gensim.corpora.dictionary.Dictionary object at 0x12c1c6aa0>, 0.09], [<gensim.corpora.dictionary.Dictionary object at 0x12c1c5630>, 0.09], [<gensim.corpora.dictionary.Dictionary object at 0x12c1c7a00>, 0.05], [<gensim.corpora.dictionary.Dictionary object at 0x12c1c5d50>, 0.09], [<gensim.corpora.dictionary.Dictionary object at 0x12c1c6920>, 0.18], [<gensim.corpora.dictionary.Dictionary object at 0x12c1c5ea0>, 0.09], [<gensim.corpora.dictionary.Dictionary object at 0x12c1c5360>, 0.09], [<gensim.corpora.dictionary.Dictionary object at 0x12c1c7130>, 0.09], [<gensim.corpora.dictionary.Dictionary object at 0x12c1c6110>, 0.09], [<gensim.corpora.di

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



KeyboardInterrupt: 